In [1]:
import numpy as np
import pandas as pd
from scipy.sparse import coo_matrix
import os
import random
from statsmodels.stats.proportion import binom_test
from statsmodels.stats.multitest import multipletests

def parse_genome(df):
    genome_id = df['#query'][0].split('_')[0]
    keggs = df['KEGG_ko'].replace('-', None).dropna()
    keggs = list(map(lambda x: x.split(','), keggs.values))
    keggs = sum(keggs, [])
    keggs = pd.DataFrame({'KEGG_ko': keggs})
    keggs['genome_id'] = genome_id
    return keggs

def to_sparse_matrix(func_df, genome_id='genome_id', kegg_id='KEGG_ko'):
    # create genome-specific index
    ogus = list(set(func_df[genome_id]))
    ogu_lookup = pd.Series(np.arange(0, len(ogus)), ogus)
    # create KEGG-specific index
    keggs = list(set(func_df[kegg_id]))
    kegg_lookup = pd.Series(np.arange(0, len(keggs)), keggs)
    # rename names as numbers
    ogu_id = func_df[genome_id].apply(lambda x: ogu_lookup.loc[x]).astype(np.int64)
    kegg_id = func_df[kegg_id].apply(lambda x: kegg_lookup.loc[x]).astype(np.int64)
    # assign the presence / absence of a gene
    func_df['count'] = 1
    c = func_df['count'].values
    # format into a matrix
    data = coo_matrix((c, (ogu_id, kegg_id)))
    ko_ogu = pd.DataFrame(data.todense(), index=ogus, columns=keggs)
    return ko_ogu

def btest(pa1, pa2, seed=0, return_proportions=False):
    """ Performs genome wide binomial test between two groups of taxa
    Parameters
    ----------
    df1 : pd.DataFrame
        Rows are taxa, columns are genes
    df2 : pd.DataFrame
        Rows are taxa, columns are genes
    Returns
    -------
    pd.Series : list of genes associated with df1
    pd.Series : list of genes associated with df2
    """
    np.random.seed(seed)
    random.seed(seed)
    #pa1 = df1 > 0
    #pa2 = df2 > 0
    idx = list(set(pa1.columns) | set(pa2.columns))
    idx.sort()
    pa1 = pa1.sum(axis=0).reindex(idx).fillna(0)
    pa2 = pa2.sum(axis=0).reindex(idx).fillna(0)
    n = pa1 + pa2
    obs = list(zip(list(pa1.values), list((pa2.values + 1) / (pa2 + 1).sum()), list(n.values)))
    pvals = pd.Series([binom_test(a, n, b, 'two-sided') for (a, b, n) in obs],
                      index=n.index)
    if return_proportions:
        res = pd.DataFrame({'groupA': pa1, 'groupB': pa2, 'pval': pvals})
        def relabel_f(x):
            if x['groupA'] < x['groupB']:
                return 'groupB'
            else:
                return 'groupA'
        res['side'] = res.apply(relabel_f, axis=1)
        return res

    return pvals

def log_pvalue(lr, alpha=0.1, filter=True):
    """ Converts pvalues to -log(pvalue)
    Also performs Boniferroni correction.
    """
    lr = lr.reset_index()
    # lr.columns = ['KEGG', 'pvalue']
    lr['-log(pvalue)'] = -np.log(lr['pvalue'] + 1e-200)
    res = multipletests(lr['pvalue'], method='fdr_bh', alpha=alpha)
    lr['pvalue_corrected'] = res[1]
    if filter:
        lr = lr.loc[res[0]]
        return lr
    return lr

from matplotlib_venn import venn2
from matplotlib import pyplot as plt
import pandas as pd

In [2]:
metadata_new = pd.read_table('../../Meta_diseases_analyses/table/eggNOG_species_rep.txt')

In [3]:
# genes of top 100 microbes -- each disease dataset
#load tables
import os
dir_str = "../../Meta_diseases_analyses/table/"
postfix = "_deseq2_all.txt"
table_names = [dir_str + _f for _f in os.listdir(dir_str) if _f.endswith(postfix)]
# table_names
results_n = {}
results_p = {}

for table_n in table_names:
    i = pd.read_table(table_n)
    i['CI_5'] = i['log2FoldChange'] - i['lfcSE']*1.96
    i['CI_95'] = i['log2FoldChange'] + i['lfcSE']*1.96
    i_negative = i.sort_values(by=['CI_95'],ascending=True).head(100)
    i_positive = i.sort_values(by=['CI_5'],ascending=False).head(100)
    disease_as_key = table_n.replace(dir_str, "").replace(postfix, "")
    results_n[disease_as_key] = i_negative["Unnamed: 0"]
    results_p[disease_as_key] = i_positive["Unnamed: 0"]

In [4]:
eggNOG_dir = 'http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalogue/'
results_n.keys()

dict_keys(['Qian_PD', 'iMSMS_MS', 'T1D', 'QinT2D', 'Zhu_Schizophrenia', 'Franzosa_CD', 'Qin_Obesity', 'Nielsen_UC', 'Laske_AD', 'ASD_250'])

In [5]:
#set(results['iMSMS_MS'])
#"{} + {} = banana".format(8, 'apple')
results = results_n
for key in results.keys():
    print (key)

Qian_PD
iMSMS_MS
T1D
QinT2D
Zhu_Schizophrenia
Franzosa_CD
Qin_Obesity
Nielsen_UC
Laske_AD
ASD_250


In [6]:
for key in results.keys():
    key_negative = set(results[key])
    key_negative_rep = metadata_new[metadata_new['Species'].isin(key_negative)]
    Species_rep_ids_key_negative = key_negative_rep['Species_rep'].drop_duplicates()
    os.mkdir('../Species_table/'+ key + '_Negative')
    for i in Species_rep_ids_key_negative:
        os.system("wget '{}/{}/{}/genome/{}_eggNOG.tsv' -O {}/{}_eggNOG.tsv".format(eggNOG_dir, i[:-2], i, i, '../Species_table/'+ key + '_Negative', i))

--2023-02-04 23:07:00--  http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalogue//MGYG0000000/MGYG000000019/genome/MGYG000000019_eggNOG.tsv
Resolving ftp.ebi.ac.uk (ftp.ebi.ac.uk)... 193.62.193.138
Connecting to ftp.ebi.ac.uk (ftp.ebi.ac.uk)|193.62.193.138|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2900073 (2.8M) [text/tab-separated-values]
Saving to: ‘../Species_table/Qian_PD_Negative/MGYG000000019_eggNOG.tsv’

     0K .......... .......... .......... .......... ..........  1%  266K 10s
    50K .......... .......... .......... .......... ..........  3%  535K 8s
   100K .......... .......... .......... .......... ..........  5% 48.4M 5s
   150K .......... .......... .......... .......... ..........  7%  533K 5s
   200K .......... .......... .......... .......... ..........  8%  529K 5s
   250K .......... .......... .......... .......... .......... 10%  516K 5s
   300K .......... .......... .......... .......... .....

   550K .......... .......... .......... .......... .......... 80%  543K 0s
   600K .......... .......... .......... .......... .......... 86% 28.3M 0s
   650K .......... .......... .......... .......... .......... 93%  539K 0s
   700K .......... .......... .......... .......... ......... 100%  523K=1.2s

2023-02-04 23:07:07 (612 KB/s) - ‘../Species_table/Qian_PD_Negative/MGYG000000277_eggNOG.tsv’ saved [767700/767700]

--2023-02-04 23:07:07--  http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalogue//MGYG0000002/MGYG000000291/genome/MGYG000000291_eggNOG.tsv
Resolving ftp.ebi.ac.uk (ftp.ebi.ac.uk)... 193.62.193.138
Connecting to ftp.ebi.ac.uk (ftp.ebi.ac.uk)|193.62.193.138|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 473657 (463K) [text/tab-separated-values]
Saving to: ‘../Species_table/Qian_PD_Negative/MGYG000000291_eggNOG.tsv’

     0K .......... .......... .......... .......... .......... 10%  264K 2s
    50K .......

     0K .......... .......... .......... .......... .......... 12%  241K 2s
    50K .......... .......... .......... .......... .......... 24%  529K 1s
   100K .......... .......... .......... .......... .......... 36% 70.1M 1s
   150K .......... .......... .......... .......... .......... 48%  532K 0s
   200K .......... .......... .......... .......... .......... 60%  526K 0s
   250K .......... .......... .......... .......... .......... 72%  542K 0s
   300K .......... .......... .......... .......... .......... 84%  530K 0s
   350K .......... .......... .......... .......... .......... 96% 63.8M 0s
   400K .......... ..                                         100%  130K=0.8s

2023-02-04 23:07:14 (532 KB/s) - ‘../Species_table/Qian_PD_Negative/MGYG000000449_eggNOG.tsv’ saved [422423/422423]

--2023-02-04 23:07:14--  http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalogue//MGYG0000004/MGYG000000457/genome/MGYG000000457_eggNOG.tsv
Resolving ftp.eb

     0K .......... .......... .......... .......... ..........  7%  264K 2s
    50K .......... .......... .......... .......... .......... 15%  529K 2s
   100K .......... .......... .......... .......... .......... 23% 47.8M 1s
   150K .......... .......... .......... .......... .......... 30%  531K 1s
   200K .......... .......... .......... .......... .......... 38%  532K 1s
   250K .......... .......... .......... .......... .......... 46%  530K 1s
   300K .......... .......... .......... .......... .......... 54%  532K 1s
   350K .......... .......... .......... .......... .......... 61% 54.6M 0s
   400K .......... .......... .......... .......... .......... 69%  538K 0s
   450K .......... .......... .......... .......... .......... 77%  532K 0s
   500K .......... .......... .......... .......... .......... 84%  540K 0s
   550K .......... .......... .......... .......... .......... 92%  533K 0s
   600K .......... .......... .......... .......... .......   100%  109M=1.0s

2023-02-0

--2023-02-04 23:07:27--  http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalogue//MGYG0000008/MGYG000000850/genome/MGYG000000850_eggNOG.tsv
Resolving ftp.ebi.ac.uk (ftp.ebi.ac.uk)... 193.62.193.138
Connecting to ftp.ebi.ac.uk (ftp.ebi.ac.uk)|193.62.193.138|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 612511 (598K) [text/tab-separated-values]
Saving to: ‘../Species_table/Qian_PD_Negative/MGYG000000850_eggNOG.tsv’

     0K .......... .......... .......... .......... ..........  8%  260K 2s
    50K .......... .......... .......... .......... .......... 16%  534K 1s
   100K .......... .......... .......... .......... .......... 25% 84.5M 1s
   150K .......... .......... .......... .......... .......... 33%  529K 1s
   200K .......... .......... .......... .......... .......... 41%  524K 1s
   250K .......... .......... .......... .......... .......... 50%  529K 1s
   300K .......... .......... .......... .......... .......

...

     0K .......... .......... .......... .......... ..........  7%  262K 2s
    50K .......... .......... .......... .......... .......... 15%  543K 2s
   100K .......... .......... .......... .......... .......... 23%  266K 2s
   150K .......... .......... .......... .......... .......... 31%  434K 1s
   200K .......... .......... .......... .......... .......... 38%  528K 1s
   250K .......... .......... .......... .......... .......... 46%  529K 1s
   300K .......... .......... .......... .......... .......... 54%  530K 1s
   350K .......... .......... .......... .......... .......... 62%  527K 1s
   400K .......... .......... .......... .......... .......... 70%  511K 0s
   450K .......... .......... .......... .......... .......... 77%  528K 0s
   500K .......... .......... .......... .......... .......... 85%  538K 0s
   550K .......... .......... .......... .......... .......... 93%  532K 0s
   600K .......... .......... .......... .......... ..        100%  460K=1.4s

2023-02-0

   800K .......... .......... .......... .......... .......... 51%  525K 2s
   850K .......... .......... .......... .......... .......... 54%  528K 2s
   900K .......... .......... .......... .......... .......... 57%  122M 1s
   950K .......... .......... .......... .......... .......... 60%  528K 1s
  1000K .......... .......... .......... .......... .......... 63%  534K 1s
  1050K .......... .......... .......... .......... .......... 66%  534K 1s
  1100K .......... .......... .......... .......... .......... 69%  531K 1s
  1150K .......... .......... .......... .......... .......... 72% 93.5M 1s
  1200K .......... .......... .......... .......... .......... 75%  536K 1s
  1250K .......... .......... .......... .......... .......... 78%  518K 1s
  1300K .......... .......... .......... .......... .......... 81%  552K 1s
  1350K .......... .......... .......... .......... .......... 84% 15.7M 0s
  1400K .......... .......... .......... .......... .......... 87%  535K 0s
  1450K ....

   200K .......... .......... .......... .......... .......... 39%  549K 1s
   250K .......... .......... .......... .......... .......... 47%  534K 1s
   300K .......... .......... .......... .......... .......... 54%  528K 1s
   350K .......... .......... .......... .......... .......... 62%  529K 1s
   400K .......... .......... .......... .......... .......... 70%  121M 0s
   450K .......... .......... .......... .......... .......... 78%  535K 0s
   500K .......... .......... .......... .......... .......... 86%  535K 0s
   550K .......... .......... .......... .......... .......... 94%  535K 0s
   600K .......... .......... .......... .......              100% 76.6M=1.2s

2023-02-04 23:34:01 (546 KB/s) - ‘../Species_table/ASD_250_Negative/MGYG000004056_eggNOG.tsv’ saved [652617/652617]

--2023-02-04 23:34:01--  http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalogue//MGYG0000040/MGYG000004064/genome/MGYG000004064_eggNOG.tsv
Resolving ftp.eb

HTTP request sent, awaiting response... 200 OK
Length: 699847 (683K) [text/tab-separated-values]
Saving to: ‘../Species_table/ASD_250_Negative/MGYG000004115_eggNOG.tsv’

     0K .......... .......... .......... .......... ..........  7%  266K 2s
    50K .......... .......... .......... .......... .......... 14%  529K 2s
   100K .......... .......... .......... .......... .......... 21%  265K 2s
   150K .......... .......... .......... .......... .......... 29%  528K 1s
   200K .......... .......... .......... .......... .......... 36%  534K 1s
   250K .......... .......... .......... .......... .......... 43%  531K 1s
   300K .......... .......... .......... .......... .......... 51%  528K 1s
   350K .......... .......... .......... .......... .......... 58%  527K 1s
   400K .......... .......... .......... .......... .......... 65%  528K 1s
   450K .......... .......... .......... .......... .......... 73%  527K 0s
   500K .......... .......... .......... .......... .......... 80%  53

    50K .......... .......... .......... .......... .......... 20%  529K 1s
   100K .......... .......... .......... .......... .......... 31%  518K 1s
   150K .......... .......... .......... .......... .......... 41%  543K 1s
   200K .......... .......... .......... .......... .......... 52%  527K 1s
   250K .......... .......... .......... .......... .......... 62%  527K 0s
   300K .......... .......... .......... .......... .......... 73%  530K 0s
   350K .......... .......... .......... .......... .......... 83%  527K 0s
   400K .......... .......... .......... .......... .......... 94%  136M 0s
   450K .......... .......... .......                         100%  288K=0.9s

2023-02-04 23:34:17 (504 KB/s) - ‘../Species_table/ASD_250_Negative/MGYG000004419_eggNOG.tsv’ saved [488903/488903]

--2023-02-04 23:34:17--  http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalogue//MGYG0000044/MGYG000004424/genome/MGYG000004424_eggNOG.tsv
Resolving ftp.eb

In [7]:
for key in results_p.keys():
    key_positive = set(results_p[key])
    key_positive_rep = metadata_new[metadata_new['Species'].isin(key_positive)]
    Species_rep_ids_key_positive = key_positive_rep['Species_rep'].drop_duplicates()
    os.mkdir('../Species_table/'+ key + '_Positive')
    for i in Species_rep_ids_key_positive:
        os.system("wget '{}/{}/{}/genome/{}_eggNOG.tsv' -O {}/{}_eggNOG.tsv".format(eggNOG_dir, i[:-2], i, i, '../Species_table/'+ key + '_Positive', i))

--2023-02-04 23:34:21--  http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalogue//MGYG0000000/MGYG000000042/genome/MGYG000000042_eggNOG.tsv
Resolving ftp.ebi.ac.uk (ftp.ebi.ac.uk)... 193.62.193.138
Connecting to ftp.ebi.ac.uk (ftp.ebi.ac.uk)|193.62.193.138|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1011621 (988K) [text/tab-separated-values]
Saving to: ‘../Species_table/Qian_PD_Positive/MGYG000000042_eggNOG.tsv’

     0K .......... .......... .......... .......... ..........  5%  265K 4s
    50K .......... .......... .......... .......... .......... 10%  531K 3s
   100K .......... .......... .......... .......... .......... 15%  265K 3s
   150K .......... .......... .......... .......... .......... 20%  526K 2s
   200K .......... .......... .......... .......... .......... 25%  528K 2s
   250K .......... .......... .......... .......... .......... 30%  521K 2s
   300K .......... .......... .......... .......... ......

   800K .......... .......... .......... .......... .......... 88%  539K 0s
   850K .......... .......... .......... .......... .......... 93%  537K 0s
   900K .......... .......... .......... .......... .......... 98% 23.2M 0s
   950K .......... ...                                        100%  152K=1.9s

2023-02-04 23:34:30 (511 KB/s) - ‘../Species_table/Qian_PD_Positive/MGYG000000080_eggNOG.tsv’ saved [987065/987065]

--2023-02-04 23:34:30--  http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalogue//MGYG0000001/MGYG000000134/genome/MGYG000000134_eggNOG.tsv
Resolving ftp.ebi.ac.uk (ftp.ebi.ac.uk)... 193.62.193.138
Connecting to ftp.ebi.ac.uk (ftp.ebi.ac.uk)|193.62.193.138|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 858434 (838K) [text/tab-separated-values]
Saving to: ‘../Species_table/Qian_PD_Positive/MGYG000000134_eggNOG.tsv’

     0K .......... .......... .......... .......... ..........  5%  233K 3s
    50K .......

   550K .......... .......... .......... .......... .......... 58%  525K 1s
   600K .......... .......... .......... .......... .......... 62%  535K 1s
   650K .......... .......... .......... .......... .......... 67% 64.0M 1s
   700K .......... .......... .......... .......... .......... 72%  531K 1s
   750K .......... .......... .......... .......... .......... 77%  528K 0s
   800K .......... .......... .......... .......... .......... 82%  525K 0s
   850K .......... .......... .......... .......... .......... 87%  532K 0s
   900K .......... .......... .......... .......... .......... 92%  124M 0s
   950K .......... .......... .......... .......... .......... 96%  531K 0s
  1000K .......... .......... .......... ..                   100%  345K=2.0s

2023-02-04 23:34:38 (521 KB/s) - ‘../Species_table/Qian_PD_Positive/MGYG000000151_eggNOG.tsv’ saved [1057110/1057110]

--2023-02-04 23:34:38--  http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalog

   600K .......... .......... .......... .......... .......... 68%  529K 1s
   650K .......... .......... .......... .......... .......... 74% 84.6M 0s
   700K .......... .......... .......... .......... .......... 79%  533K 0s
   750K .......... .......... .......... .......... .......... 84%  534K 0s
   800K .......... .......... .......... .......... .......... 89%  532K 0s
   850K .......... .......... .......... .......... .......... 95%  488K 0s
   900K .......... .......... .......... .......... .....     100% 60.0M=1.8s

2023-02-04 23:34:46 (524 KB/s) - ‘../Species_table/Qian_PD_Positive/MGYG000000221_eggNOG.tsv’ saved [967859/967859]

--2023-02-04 23:34:46--  http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalogue//MGYG0000002/MGYG000000268/genome/MGYG000000268_eggNOG.tsv
Resolving ftp.ebi.ac.uk (ftp.ebi.ac.uk)... 193.62.193.138
Connecting to ftp.ebi.ac.uk (ftp.ebi.ac.uk)|193.62.193.138|:80... connected.
HTTP request sent, awaiting respo

Connecting to ftp.ebi.ac.uk (ftp.ebi.ac.uk)|193.62.193.138|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 497153 (486K) [text/tab-separated-values]
Saving to: ‘../Species_table/Qian_PD_Positive/MGYG000000522_eggNOG.tsv’

     0K .......... .......... .......... .......... .......... 10%  265K 2s
    50K .......... .......... .......... .......... .......... 20%  526K 1s
   100K .......... .......... .......... .......... .......... 30%  265K 1s
   150K .......... .......... .......... .......... .......... 41%  516K 1s
   200K .......... .......... .......... .......... .......... 51%  530K 1s
   250K .......... .......... .......... .......... .......... 61%  529K 0s
   300K .......... .......... .......... .......... .......... 72%  529K 0s
   350K .......... .......... .......... .......... .......... 82%  532K 0s
   400K .......... .......... .......... .......... .......... 92%  526K 0s
   450K .......... .......... .......... .....                100%  3

...

     0K .......... .......... .......... .......... ..........  8%  267K 2s
    50K .......... .......... .......... .......... .......... 16%  530K 1s
   100K .......... .......... .......... .......... .......... 25% 84.0M 1s
   150K .......... .......... .......... .......... .......... 33%  529K 1s
   200K .......... .......... .......... .......... .......... 41%  529K 1s
   250K .......... .......... .......... .......... .......... 50%  532K 1s
   300K .......... .......... .......... .......... .......... 58%  533K 0s
   350K .......... .......... .......... .......... .......... 66% 19.1M 0s
   400K .......... .......... .......... .......... .......... 75%  533K 0s
   450K .......... .......... .......... .......... .......... 83%  536K 0s
   500K .......... .......... .......... .......... .......... 92%  525K 0s
   550K .......... .......... .......... .......... .......   100%  137M=0.9s

2023-02-05 09:50:26 (632 KB/s) - ‘../Species_table/ASD_250_Positive/MGYG000003248_egg

--2023-02-05 09:50:33--  http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalogue//MGYG0000034/MGYG000003460/genome/MGYG000003460_eggNOG.tsv
Resolving ftp.ebi.ac.uk (ftp.ebi.ac.uk)... 193.62.193.138
Connecting to ftp.ebi.ac.uk (ftp.ebi.ac.uk)|193.62.193.138|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 642003 (627K) [text/tab-separated-values]
Saving to: ‘../Species_table/ASD_250_Positive/MGYG000003460_eggNOG.tsv’

     0K .......... .......... .......... .......... ..........  7%  264K 2s
    50K .......... .......... .......... .......... .......... 15%  528K 1s
   100K .......... .......... .......... .......... .......... 23% 86.3M 1s
   150K .......... .......... .......... .......... .......... 31%  535K 1s
   200K .......... .......... .......... .......... .......... 39%  513K 1s
   250K .......... .......... .......... .......... .......... 47%  539K 1s
   300K .......... .......... .......... .......... .......

   450K .......... .......... .......... .......... .......... 46%  543K 1s
   500K .......... .......... .......... .......... .......... 51%  537K 1s
   550K .......... .......... .......... .......... .......... 56%  512K 1s
   600K .......... .......... .......... .......... .......... 60% 99.0M 1s
   650K .......... .......... .......... .......... .......... 65%  549K 1s
   700K .......... .......... .......... .......... .......... 70%  541K 1s
   750K .......... .......... .......... .......... .......... 74%  536K 0s
   800K .......... .......... .......... .......... .......... 79% 15.2M 0s
   850K .......... .......... .......... .......... .......... 84%  529K 0s
   900K .......... .......... .......... .......... .......... 88%  537K 0s
   950K .......... .......... .......... .......... .......... 93%  539K 0s
  1000K .......... .......... .......... .......... .......... 98%  558K 0s
  1050K .......... .......... .                               100% 6.50M=1.7s

2023-02-0

   450K .......... .......... .......... .......... .......... 68%  538K 1s
   500K .......... .......... .......... .......... .......... 75%  530K 0s
   550K .......... .......... .......... .......... .......... 82%  516K 0s
   600K .......... .......... .......... .......... .......... 89%  543K 0s
   650K .......... .......... .......... .......... .......... 96%  513K 0s
   700K .......... .......... ........                        100% 74.5M=1.5s

2023-02-05 09:50:50 (484 KB/s) - ‘../Species_table/ASD_250_Positive/MGYG000004345_eggNOG.tsv’ saved [746081/746081]

--2023-02-05 09:50:50--  http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalogue//MGYG0000043/MGYG000004390/genome/MGYG000004390_eggNOG.tsv
Resolving ftp.ebi.ac.uk (ftp.ebi.ac.uk)... 193.62.193.138
Connecting to ftp.ebi.ac.uk (ftp.ebi.ac.uk)|193.62.193.138|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 800193 (781K) [text/tab-separated-values]
Saving to: ‘

   700K .......... .......... .......... .......... .......... 96%  525K 0s
   750K .......... .......... .....                           100%  107M=1.2s

2023-02-05 09:50:58 (636 KB/s) - ‘../Species_table/ASD_250_Positive/MGYG000004581_eggNOG.tsv’ saved [794502/794502]

--2023-02-05 09:50:58--  http://ftp.ebi.ac.uk/pub/databases/metagenomics/mgnify_genomes/human-gut/v2.0/species_catalogue//MGYG0000046/MGYG000004640/genome/MGYG000004640_eggNOG.tsv
Resolving ftp.ebi.ac.uk (ftp.ebi.ac.uk)... 193.62.193.138
Connecting to ftp.ebi.ac.uk (ftp.ebi.ac.uk)|193.62.193.138|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 662390 (647K) [text/tab-separated-values]
Saving to: ‘../Species_table/ASD_250_Positive/MGYG000004640_eggNOG.tsv’

     0K .......... .......... .......... .......... ..........  7%  229K 3s
    50K .......... .......... .......... .......... .......... 15%  543K 2s
   100K .......... .......... .......... .......... .......... 23%  508K 1s
   150K .......

In [8]:
for key in results_p.keys():
    key_positive = set(results_p[key])
    key_positive_rep = metadata_new[metadata_new['Species'].isin(key_positive)]
    Species_rep_ids_key_positive = key_positive_rep['Species_rep'].drop_duplicates()

In [10]:
for key in results_p.keys():
    key_positive = set(results_p[key])
    key_positive_rep = metadata_new[metadata_new['Species'].isin(key_positive)]
    Species_rep_ids_key_positive = key_positive_rep['Species_rep'].drop_duplicates()
    df_list_p = []
    for i in Species_rep_ids_key_positive:
        f_name = '../Species_table/{}_Positive/{}_eggNOG.tsv'.format(key,i)
        #f_name = key + '_Positive/{}_eggNOG.tsv'.format(i)
        df_parsed = parse_genome(pd.read_table(f_name))
        df_list_p.append(df_parsed)
    
    df_cat_p = pd.concat(df_list_p, axis=0)
    genome_kegg_counts_p = to_sparse_matrix(df_cat_p)
    genome_kegg_counts_p.to_csv('table/genome_kegg_counts_p_{}.txt'.format(key), sep = '\t') 

In [11]:
for key in results_n.keys():
    key_negative = set(results_n[key])
    key_negative_rep = metadata_new[metadata_new['Species'].isin(key_negative)]
    key_negative_rep = key_negative_rep.loc[key_negative_rep['Species_rep'] != 'MGYG000001406.1']
    key_negative_rep = key_negative_rep.loc[key_negative_rep['Species_rep'] != 'MGYG000001455.1']
    key_negative_rep = key_negative_rep.loc[key_negative_rep['Species_rep'] != 'MGYG000002950.1']
    Species_rep_ids_key_negative = key_negative_rep['Species_rep'].drop_duplicates()
    df_list_n = []
    for i in Species_rep_ids_key_negative:
        f_name = '../Species_table/{}_Negative/{}_eggNOG.tsv'.format(key,i)
        df_parsed = parse_genome(pd.read_table(f_name))
#         try:
#             df_parsed = parse_genome(pd.read_table(f_name))
#         except Exception as e:
#             print(f_name, i, key)
#             raise e
        df_list_n.append(df_parsed)
    
    df_cat_n = pd.concat(df_list_n, axis=0)
    genome_kegg_counts_n = to_sparse_matrix(df_cat_n)
    genome_kegg_counts_n.to_csv('table/genome_kegg_counts_n_{}.txt'.format(key), sep = '\t') 

In [12]:
#compare negative and negative: from top 100 microbes
for key in results_n.keys():
    f_name_p = 'table/genome_kegg_counts_p_{}.txt'.format(key)
    f_name_n = 'table/genome_kegg_counts_n_{}.txt'.format(key)
    genome_kegg_counts_p = pd.read_table(f_name_p, sep = '\t', index_col=0)
    genome_kegg_counts_n = pd.read_table(f_name_n, sep = '\t', index_col=0)
#     try:
#         kegg2 = btest(genome_kegg_counts_p, genome_kegg_counts_n, return_proportions=True)
#     except Exception as e:
#         print(key)
#         print(f_name_n)
#         print(f_name_p)
#         genome_kegg_counts_xyz = pd.read_table(f_name_n, sep = '\t', index_col=0)
#         print(genome_kegg_counts_xyz)
#         raise e
    kegg2 = btest(genome_kegg_counts_p, genome_kegg_counts_n, return_proportions=True)
    kegg2 = kegg2.loc[kegg2['side'] == 'groupB']
    kegg2 = kegg2.loc[kegg2['pval'] <= 0.001]
    kegg2.to_csv('../table_abundant_genes/kegg_more_abundant_in_cases_{}.txt'.format(key), sep = '\t')

In [67]:
key_genes = {}
for key in results_n.keys():
    f_name = '../table_abundant_genes/kegg_more_abundant_in_cases_{}.txt'.format(key)
    gene_table = pd.read_table(f_name, sep = '\t', index_col=0)
    key_genes[key] = set(gene_table.index)

In [68]:
len(key_genes['Laske_AD'])

1212

In [69]:
results_n.keys()

dict_keys(['Qian_PD', 'iMSMS_MS', 'T1D', 'QinT2D', 'Zhu_Schizophrenia', 'Franzosa_CD', 'Qin_Obesity', 'Nielsen_UC', 'Laske_AD', 'ASD_250'])

In [72]:
for i in results_n: 
    other_keys = [_key for _key in results_n if _key != i]
    i_genes = key_genes[i] - (set.union(*[key_genes[key] for key in other_keys]))
    i_genes = list(i_genes)
    pd.DataFrame(i_genes).to_csv('../disease_specific_genes/{}_genes.txt'.format(i), sep = '\t') 
    len(i_genes)

In [73]:
len(Laske_AD_genes)

48

In [93]:
#type(Laske_AD_genes)

Laske_ad_cases = pd.read_table('../table_abundant_genes/kegg_more_abundant_in_cases_Laske_AD.txt')
Laske_ad_case_specific = Laske_ad_cases.loc[Laske_ad_cases['Unnamed: 0'].isin(Laske_AD_genes)]
Laske_ad_case_specific.sort_values(by=['pval'],ascending=True)

Unnamed: 0  groupA  groupB          pval    side
1176  ko:K21563     5.0     7.0  6.244054e-19  groupB
773   ko:K08298     4.0    15.0  8.116928e-13  groupB
860   ko:K10242     3.0     4.0  1.861210e-12  groupB
350   ko:K02568     3.0     4.0  1.861210e-12  groupB
559   ko:K05882     3.0     4.0  1.861210e-12  groupB
75    ko:K00446     2.0     3.0  9.050476e-09  groupB
943   ko:K12567     1.0     2.0  6.768953e-05  groupB
935   ko:K12262     1.0     2.0  6.768953e-05  groupB
916   ko:K11731     1.0     2.0  6.768953e-05  groupB
1149  ko:K20431     1.0     2.0  6.768953e-05  groupB
567   ko:K05996     1.0     2.0  6.768953e-05  groupB
850   ko:K09958     1.0     2.0  6.768953e-05  groupB
1161  ko:K20940     1.0     2.0  6.768953e-05  groupB
1078  ko:K17592     1.0     2.0  6.768953e-05  groupB
1100  ko:K18363     1.0     2.0  6.768953e-05  groupB
748   ko:K07746     1.0     2.0  6.768953e-05  groupB
740   ko:K07709     1.0     2.0  6.768953e-05  groupB
1165  ko:K21309     1.0     2.0  6.768953e-05  groupB
664   ko:K07046     1.0     2.0  6.768953e-05  groupB
1147  ko:K20421     1.0     2.0  6.768953e-05  groupB
686   ko:K07231     1.0     2.0  6.768953e-05  groupB
555   ko:K05818     1.0     2.0  6.768953e-05  groupB
436   ko:K03611     1.0     2.0  6.768953e-05  groupB
19    ko:K00141     1.0     2.0  6.768953e-05  groupB
40    ko:K00257     1.0     2.0  6.768953e-05  groupB
1191  ko:K21963     1.0     2.0  6.768953e-05  groupB
1168  ko:K21440     1.0     2.0  6.768953e-05  groupB
76    ko:K00479     1.0     2.0  6.768953e-05  groupB
77    ko:K00480     1.0     2.0  6.768953e-05  groupB
1125  ko:K19186     1.0     2.0  6.768953e-05  groupB
145   ko:K01003     1.0     2.0  6.768953e-05  groupB
243   ko:K01800     1.0     2.0  6.768953e-05  groupB
247   ko:K01826     1.0     2.0  6.768953e-05  groupB
292   ko:K02234     1.0     2.0  6.768953e-05  groupB
356   ko:K02613     1.0     2.0  6.768953e-05  groupB
388   ko:K03119     1.0     2.0  6.768953e-05  groupB
402   ko:K03428     1.0     2.0  6.768953e-05  groupB
205   ko:K01463     1.0     2.0  6.768953e-05  groupB
1134  ko:K19349     1.0     2.0  6.768953e-05  groupB
17    ko:K00114     1.0     3.0  1.203342e-04  groupB
801   ko:K09020     1.0     3.0  1.203342e-04  groupB
1197  ko:K22226     1.0     3.0  1.203342e-04  groupB
69    ko:K00356     1.0     3.0  1.203342e-04  groupB
49    ko:K00329     1.0     3.0  1.203342e-04  groupB
42    ko:K00274     1.0     3.0  1.203342e-04  groupB
1007  ko:K14647     1.0     3.0  1.203342e-04  groupB
1199  ko:K22300     1.0     3.0  1.203342e-04  groupB
869   ko:K10550     1.0     4.0  1.880166e-04  groupB

In [74]:
len(Qian_PD_genes)

620

In [75]:
len(iMSMS_MS_genes)

65

In [76]:
len(T1D_genes)

49

In [77]:
len(QinT2D_genes)

18

In [78]:
len(Zhu_Schizophrenia_genes)

106

In [79]:
len(Franzosa_CD_genes)

57

In [80]:
len(Qin_Obesity_genes)

35

In [81]:
len(Nielsen_UC_genes)

138

In [82]:
len(ASD_250_genes)

63